# Airbnb London September 2023 Analysis
    Author: Furkan Cantürk
    Date: December 1, 2023

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from ipywidgets import HBox

pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 200)

### Reading Data

In [2]:
listings_summary = pd.read_csv('listings.csv')
listings_summary = listings_summary.set_index('id').sort_index()

listings = pd.read_csv('listings.csv.gz', compression='gzip')
calendar = pd.read_csv('calendar.csv.gz', compression='gzip')

#reviews = pd.read_csv('reviews.csv.gz', compression='gzip', chunksize=1000)

C:\Users\serda\AppData\Local\Temp\ipykernel_13772\3592087495.py:1: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  listings_summary = pd.read_csv('listings.csv')
C:\Users\serda\AppData\Local\Temp\ipykernel_13772\3592087495.py:4: DtypeWarning: Columns (68) have mixed types. Specify dtype option on import or set low_memory=False.
  listings = pd.read_csv('listings.csv.gz', compression='gzip')


Q1) What is the portion of listings having extremely low or high prices?

In [3]:
# Lots of outliers observed even only prices less than 1000 showed
fig1 = px.violin(listings_summary[listings_summary.price < 1000], y='price', x='room_type')

fig1.update_layout(title = 'Price (< 1000) Distributions of Room Types', title_x = 0.5)

fig1.show()

In [4]:
# Isolation Forest Algorithm to detect anomalies
from sklearn.ensemble import IsolationForest

listings_summary['price_anomaly'] = np.nan

room_grouped_listings = listings_summary.groupby('room_type')

# anomaly detection separately for each room_type
for room_type in listings_summary.room_type.unique():
    model = IsolationForest(n_jobs=-1)

    prices = room_grouped_listings['price'].get_group(room_type).values.reshape(-1,1)

    pred = model.fit_predict(prices) 
    
    listings_summary.loc[listings_summary['room_type'] == room_type, 'price_anomaly'] = pred


# Visualization of price distribution cleansed from anomalies 
fig2 = px.violin(listings_summary[listings_summary['price_anomaly']==1], y='price', x='room_type')
fig2.update_layout(title = 'Price Distributions of Room Types without Anomalies', title_x = 0.5)

fig2.show()

print("RESULT: Portion of price anomalies:", sum(pred==-1) / len(pred))

RESULT: Portion of price anomalies: 0.14058956916099774


Q2) Which neigbourhood(s) have high count of listings, high prices and low ratings? (This question helps understanding where customers are relatively less satisfied.)

In [8]:
# calculating median prices of room types in each neighbourhood
neighbourhood_room_type_price =  listings_summary.groupby(['neighbourhood', 'room_type'])['price'].agg('median').unstack()

# calculating mean prices of room types in each neighbourhood
listings_summary = listings_summary.merge(listings[['id', 'review_scores_rating']], on='id')
neighbourhood_room_type_rating =  listings_summary.groupby(['neighbourhood', 'room_type'])['review_scores_rating'].agg('mean').unstack()

# calculating counts of accommodations for each room type in each neighbourhood
neighbourhood_listing_count = listings_summary.groupby(['neighbourhood', 'room_type']).size().unstack()


In [47]:
# concatenation of the dataframes for the calculated three metrics 
neighbourhood_room_type_metrics = {}
for room_type in listings_summary.room_type.unique():

    neighbourhood_room_type_metrics[room_type] =  pd.concat((neighbourhood_listing_count[room_type], neighbourhood_room_type_price[room_type], neighbourhood_room_type_rating[room_type]), axis=1)
    neighbourhood_room_type_metrics[room_type].columns = ['listing_count', 'price', 'rating']

neighbourhood_room_type_metrics = pd.concat(neighbourhood_room_type_metrics)

#Visualization of the calculations
figs = []
for room_type in listings_summary.room_type.unique():
    fig = px.scatter_3d(neighbourhood_room_type_metrics.loc[room_type].reset_index(),
                x='price',
                y='listing_count',
                z='rating',
                hover_data = 'neighbourhood')

    fig.update_layout(width = 400, 
                      height = 400, 
                      title=room_type, 
                      title_x=0.5,
                      margin=dict( l = 0, r = 0, b = 20, t = 50)
    )
    fig = go.FigureWidget(fig)
    figs.append(fig)

    df = neighbourhood_room_type_metrics.loc[room_type]
    compound_metric_df = df['listing_count'] * df['price'] / df['rating']
    print(f'First two ranks based on the compound metric (listing_count * price / rating) for {room_type}:')
    print(compound_metric_df.sort_values(ascending=False).head(2))
    print()
print('RESULT: There are lots of listings of private room, entire home, and shared room accomodations in Westminster but with high prices and low ratings.')
print('So, the listings in Westminster should be improved for better customer experience.')
HBox(figs)

First two ranks based on the compound metric (listing_count * price / rating) for Private room:
neighbourhood
Westminster      43286.019044
Tower Hamlets    37475.127491
dtype: float64

First two ranks based on the compound metric (listing_count * price / rating) for Entire home/apt:
neighbourhood
Westminster               390412.931367
Kensington and Chelsea    220503.969427
dtype: float64

First two ranks based on the compound metric (listing_count * price / rating) for Hotel room:
neighbourhood
Kensington and Chelsea    4503.537736
Westminster               3538.707170
dtype: float64

First two ranks based on the compound metric (listing_count * price / rating) for Shared room:
neighbourhood
Westminster    588.779070
Camden         393.511989
dtype: float64

RESULT: There are lots of listings of private room, entire home, and shared room accomodations in Westminster but with high prices and low ratings.
So, the listings in Westminster should be improved for better customer experienc

    'data': [{'customdata': array([['Barking and Dagenham'],
                   …

Q3) Are response rate or acceptance rate of hosts correlated with their counts of listings?

In [13]:
listings['host_response_rate'] = listings['host_response_rate'].apply(lambda val: float(val.replace('%', '')) if not pd.isnull(val) else val)
listings['host_acceptance_rate'] = listings['host_acceptance_rate'].apply(lambda val: float(val.replace('%', '')) if not pd.isnull(val) else val)

In [14]:
host_acceptance_rates = listings.groupby('host_id')['host_acceptance_rate'].mean()
host_response_rates = listings.groupby('host_id')['host_response_rate'].mean()
host_listing_counts = listings.groupby('host_id')['host_total_listings_count'].mean()

host_listing_count_and_acceptance = pd.concat([host_listing_counts, host_acceptance_rates, host_response_rates], axis=1)

print("The counts of listings by hosts are not correlated with their acceptance and response rate:")
print(host_listing_count_and_acceptance[['host_total_listings_count', 'host_acceptance_rate', 'host_response_rate']].corr('spearman'))

The counts of listings by hosts are not correlated with their acceptance and response rate:
                           host_total_listings_count  host_acceptance_rate  \
host_total_listings_count                   1.000000              0.057565   
host_acceptance_rate                        0.057565              1.000000   
host_response_rate                         -0.033609              0.314100   

                           host_response_rate  
host_total_listings_count           -0.033609  
host_acceptance_rate                 0.314100  
host_response_rate                   1.000000  


Q4) What is the price range of most available accomodations in a year for each room type?

In [15]:
listings_summary = listings_summary.merge(listings[['id', 'accommodates']], on='id')
listings_summary = listings_summary.set_index('id').sort_index()
listings_summary['price_per_person'] = listings_summary['price'] / listings_summary['accommodates']

In [16]:
price_bins_by_room_type = {}

# price ranges are determined separately for each room type
for room_type in listings_summary['room_type'].unique():

    # listings with price anomalies are out of analysis
    mask = (listings_summary['price_anomaly'] == 1) & (listings_summary['room_type'] == room_type)

    bin_labels, bins = pd.cut(listings_summary.loc[mask, 'price_per_person'], bins=10, retbins=True, labels=range(10))

    listings_summary.loc[mask, 'price_bin_label'] = bin_labels
    price_bins_by_room_type[room_type] = bins


pd.set_option('expand_frame_repr', False)
price_bin_avg_availability = listings_summary.groupby(['room_type', 'price_bin_label'])['availability_365'].mean().unstack()
print("The average number of available days for listings in each price (per person) bin:\n")
print(price_bin_avg_availability)

print("\nThe price ranges of the most available accomodations in a year:\n")
max_available_price_bin_labels = price_bin_avg_availability.idxmax(axis=1)

for room_type in listings_summary['room_type'].unique():
    price_bin_label = max_available_price_bin_labels[room_type]
    price_bins = price_bins_by_room_type[room_type]
    print(room_type, ":", price_bins[price_bin_label-1:price_bin_label+1])


The average number of available days for listings in each price (per person) bin:

price_bin_label           0           1           2           3           4           5           6           7           8           9
room_type                                                                                                                              
Entire home/apt   95.142319  129.255620  150.296410  171.304666  169.276498  170.810811  235.750000  159.000000  250.200000  151.333333
Hotel room       266.957447  181.352941  250.565217  156.000000  171.666667  324.500000    0.000000    0.000000         NaN    0.000000
Private room      44.612368   74.170085  122.405010  139.040548  149.319438  151.979192  152.274268  150.934169  161.793522  166.795699
Shared room      112.113924   62.604396  127.946237  146.260870  159.894737   56.750000  194.571429   20.000000  273.700000    0.000000

The price ranges of the most available accomodations in a year:

Private room : [ 98.76923077 110.88

Q5) What is the cheapest (in terms of price per person) property types in each neighbourhood? What are the average prices per person of the cheapest property types?

In [17]:
# property_type feature includes a text comprising of neighbourhood and property type information. 
# Only property type information extracted from property_type.
listings['property_type_cleaned'] = listings['property_type'].str.split(' in ', expand=True).apply(lambda row: row[0].lower() if row[1] is None else row[1].lower(), axis=1)

# Mapping property_type_cleaned from listings dataframe to listings_summary dataframe based on listing id
listings_summary['property_type'] = listings_summary.index.map(pd.Series(listings['property_type_cleaned'].values, index=listings['id'].values))

In [18]:
property_types_avg_prices =  listings_summary[listings_summary['price_anomaly'] == 1].groupby(['neighbourhood', 'property_type'])['price_per_person'].mean().unstack()

cheapest_property_types = property_types_avg_prices.idxmin(axis=1)
cheapest_property_types_prices = property_types_avg_prices.min(axis=1)
result = pd.concat((cheapest_property_types, cheapest_property_types_prices), axis=1)
result.columns = ['cheapest_property_type', 'avg_price_per_person']

print("The cheapest property type in each neighbourhood")
result

The cheapest property type in each neighbourhood


cheapest_property_type  avg_price_per_person
neighbourhood                                                      
Barking and Dagenham                tiny home              7.200000
Barnet                               bungalow             15.000000
Bexley                            guest suite             21.250000
Brent                           vacation home             18.750000
Bromley                                  tent             16.666667
Camden                                  floor             19.666667
City of London                          hotel              5.437500
Croydon                  entire vacation home             14.000000
Ealing                                    hut             19.750000
Enfield                          private room             26.250000
Greenwich                               hotel              4.250000
Hackney                               cottage             22.000000
Hammersmith and Fulham                  hotel              2.687500
Haringey                          shared room             15.000000
Harrow                   entire vacation home             23.750000
Havering                           guesthouse             19.000000
Hillingdon                              villa             12.857143
Hounslow                         private room             23.625000
Islington                            bungalow             24.500000
Kensington and Chelsea                 hostel             10.333333
Kingston upon Thames            vacation home             17.500000
Lambeth                                  yurt             13.500000
Lewisham                      entire bungalow             17.000000
Merton                        casa particular             22.750000
Newham                           private room             20.000000
Redbridge                        private room             17.500000
Richmond upon Thames             earthen home             17.500000
Southwark                          guesthouse              8.500000
Sutton                             lighthouse             12.250000
Tower Hamlets                       tiny home             20.000000
Waltham Forest                   nature lodge             17.500000
Wandsworth                           bungalow             15.500000
Westminster                            island             15.333333

Q6) Do verified hosts receive better review scores than unverified ones?

In [19]:
from scipy.stats import ttest_ind

score_types = ['review_scores_rating', 'review_scores_cleanliness', 'review_scores_accuracy', 'review_scores_communication', 'review_scores_checkin']

for score_type in score_types:

    verified_host_scores = listings.loc[listings['host_identity_verified'] == 't', score_type].dropna()
    unverified_host_scores = listings.loc[listings['host_identity_verified'] == 'f', score_type].dropna()
    
    print(f"Mean {score_type} of {len(verified_host_scores)} verified hosts: ", verified_host_scores.mean())
    print(f"Mean {score_type} of {len(unverified_host_scores)} unverified hosts: ", unverified_host_scores.mean())
   
    stat1, pval1 = ttest_ind(verified_host_scores, unverified_host_scores, alternative='greater')

    if pval1 < 0.05:
        print(f'Yes, verified hosts have significantly higher review scores than unverified hosts (p < {pval1})')
    else:
        print(f'No, verified hosts don\'t have significantly higher review scores than unverified hosts (p < {pval1})')

    print("***************")

Mean review_scores_rating of 59130 verified hosts:  4.621970573313039
Mean review_scores_rating of 6658 unverified hosts:  4.370692400120157
Yes, verified hosts have significantly higher review scores than unverified hosts (p < 7.614303698079195e-149)
***************
Mean review_scores_cleanliness of 58571 verified hosts:  4.629481825476772
Mean review_scores_cleanliness of 6294 unverified hosts:  4.566108992691452
Yes, verified hosts have significantly higher review scores than unverified hosts (p < 2.1254114579227957e-18)
***************
Mean review_scores_accuracy of 58562 verified hosts:  4.714746593354053
Mean review_scores_accuracy of 6291 unverified hosts:  4.694473056747735
Yes, verified hosts have significantly higher review scores than unverified hosts (p < 0.0011384134001447587)
***************
Mean review_scores_communication of 58561 verified hosts:  4.801734943050835
Mean review_scores_communication of 6290 unverified hosts:  4.772402225755167
Yes, verified hosts have sig

Q7) Do instant bookable accomodations have lower review scores than not instant ones?

In [20]:
from scipy.stats import ttest_ind

score_types = ['review_scores_rating', 'review_scores_cleanliness', 'review_scores_accuracy', 'review_scores_communication', 'review_scores_checkin']

for score_type in score_types:

    instant_bookable_scores = listings.loc[listings['instant_bookable'] == 't', score_type].dropna()
    not_instant_bookable_scores = listings.loc[listings['instant_bookable'] == 'f', score_type].dropna()
    
    print(f"Mean {score_type} of {len(instant_bookable_scores)} instant bookable accomodations: ", instant_bookable_scores.mean())
    print(f"Mean {score_type} of {len(not_instant_bookable_scores)} not instant bookable accomodations: ", not_instant_bookable_scores.mean())
   
    stat1, pval1 = ttest_ind(instant_bookable_scores, not_instant_bookable_scores, alternative='less')

    if pval1 < 0.05:
        print(f'Yes, instant bookable accomodations have significantly lower review scores than others (p < {pval1})')
    else:
        print(f'No, instant bookable accomodations don\'t have significantly lower review scores than others (p < {pval1})')

    print("***************")

Mean review_scores_rating of 18606 instant bookable accomodations:  4.497276147479308
Mean review_scores_rating of 47182 not instant bookable accomodations:  4.6356845831037266
Yes, instant bookable accomodations have significantly lower review scores than others (p < 2.8467376001867136e-101)
***************
Mean review_scores_cleanliness of 18361 instant bookable accomodations:  4.54807145580306
Mean review_scores_cleanliness of 46504 not instant bookable accomodations:  4.653047694821951
Yes, instant bookable accomodations have significantly lower review scores than others (p < 1.4170567787184738e-106)
***************
Mean review_scores_accuracy of 18357 instant bookable accomodations:  4.617646129541864
Mean review_scores_accuracy of 46496 not instant bookable accomodations:  4.750339599105299
Yes, instant bookable accomodations have significantly lower review scores than others (p < 1.0100523261402445e-204)
***************
Mean review_scores_communication of 18359 instant bookable 

Q8) Do superhosts receive better review scores than others?

In [21]:
from scipy.stats import ttest_ind

score_types = ['review_scores_rating', 'review_scores_cleanliness', 'review_scores_accuracy', 'review_scores_communication', 'review_scores_checkin']

for score_type in score_types:

    superhost_scores = listings.loc[listings['host_is_superhost'] == 't', score_type].dropna()
    not_superhost_scores = listings.loc[listings['host_is_superhost'] == 'f', score_type].dropna()
    
    print(f"Mean {score_type} of {len(instant_bookable_scores)} instant bookable accomodations: ", instant_bookable_scores.mean())
    print(f"Mean {score_type} of {len(not_instant_bookable_scores)} not instant bookable accomodations: ", not_instant_bookable_scores.mean())
   
    stat1, pval1 = ttest_ind(instant_bookable_scores, not_instant_bookable_scores, alternative='greater')

    if pval1 < 0.05:
        print(f'Yes, superhosts have significantly higher review scores than others (p < {pval1})')
    else:
        print(f'No, superhosts accomodations don\'t have significantly higher review scores than others (p < {pval1})')

    print("***************")

Mean review_scores_rating of 18354 instant bookable accomodations:  4.7172747085104065
Mean review_scores_rating of 46467 not instant bookable accomodations:  4.801023091656445
No, superhosts accomodations don't have significantly higher review scores than others (p < 1.0)
***************
Mean review_scores_cleanliness of 18354 instant bookable accomodations:  4.7172747085104065
Mean review_scores_cleanliness of 46467 not instant bookable accomodations:  4.801023091656445
No, superhosts accomodations don't have significantly higher review scores than others (p < 1.0)
***************
Mean review_scores_accuracy of 18354 instant bookable accomodations:  4.7172747085104065
Mean review_scores_accuracy of 46467 not instant bookable accomodations:  4.801023091656445
No, superhosts accomodations don't have significantly higher review scores than others (p < 1.0)
***************
Mean review_scores_communication of 18354 instant bookable accomodations:  4.7172747085104065
Mean review_scores_com

Q9) Can we say if an accomodation has higher number of reviews, it is likely to have more negative reviews, without reading the reviews?

In [22]:
print("Correlation of number_of_reviews with each review score type:")
print(listings[['number_of_reviews'] + score_types].corr('spearman')['number_of_reviews'])

print("\n It is observed that the number of reviews has some negative correlation with review scores.\n\
So, we can say that the more reviews are, the more negative they are, without reading the reviews.")

Correlation of number_of_reviews with each review score type:
number_of_reviews              1.000000
review_scores_rating          -0.156273
review_scores_cleanliness     -0.164638
review_scores_accuracy        -0.230677
review_scores_communication   -0.301651
review_scores_checkin         -0.281671
Name: number_of_reviews, dtype: float64

 It is observed that the number of reviews has some negative correlation with review scores.
So, we can say that the more reviews are, the more negative they are, without reading the reviews.


Q10) Which month accomodations are most available in each neighbourhood?

In [23]:
calendar['month'] = calendar['date'].apply(lambda str_date: pd.Timestamp(str_date).month)

# listings_summary = listings_summary.set_index('id').sort_index()

calendar['neighbourhood'] = calendar['listing_id'].map(listings_summary['neighbourhood'])

print('Calendar lengths and Number of listings ')
print(calendar.groupby('listing_id').size().value_counts()) 

Calendar lengths and Number of listings 
365    87873
366       73
Name: count, dtype: int64


In [25]:
# We see that calendar composes one year of each listing begining from September 2023 to September 2024.
# So, we can directly count the total number of available accomodations for each month.

total_available_accomodations = calendar.groupby(['neighbourhood', 'month', 'available']).size().unstack()['t'].unstack()

print("Total number of available accomodations on each month:")
print(total_available_accomodations.head(5))

print("\nThe most available month for each neighbourhod:")
result = total_available_accomodations.idxmax(axis=1)
print(result)

Total number of available accomodations on each month:
month                    1      2      3      4      5      6      7      8      9      10     11     12
neighbourhood                                                                                           
Barking and Dagenham   9240   8813   7964   7609   7934   6824   7154   7171   6769   9456   9995   8986
Barnet                32282  30518  27602  26486  27356  22623  23646  23584  23005  31874  35189  31166
Bexley                10116   9621   8497   8112   8342   7123   7373   7440   7097   9526  10290   9659
Brent                 36081  33912  29912  28453  30134  24941  28091  27425  23075  33196  37362  34093
Bromley               11783  11508  10272   9768  10191   7838   8097   8249   8205  11353  12534  11207

The most available month for each neighbourhod:
neighbourhood
Barking and Dagenham      11
Barnet                    11
Bexley                    11
Brent                     11
Bromley                   11
Ca